# Summary
In this notebook, all the probability tables are shown that match the bgc and chemical classes based on MIBiG. Highest values per column are coloured in green.

In [1]:
import os
import urllib
import glob
import json
import time
import numpy as np
import pandas as pd
from collections import OrderedDict

## Loading the data

In [2]:
mibig_folder = "/mnt/scratch/louwe015/mibig_json_2.0/"

base_path = "/mnt/scratch/louwe015/NPLinker/classifying/mibig_classifications/"
out_base = os.path.split(base_path[:-1])[0]
mibig_classes = os.path.join(out_base, "MIBiG2.0_compounds_with_AS_BGC_CF_NPC_classes.txt")
print("mibig_classes exists is", os.path.isfile(mibig_classes))

mibig_classes exists is True


In [6]:
classes_dict = {}
with open(mibig_classes) as inf:
    header = inf.readline()
    for line in inf:
        elems = line.strip().split("\t")
        chem_id = elems.pop(0)
        class_base = elems.pop(0).split(',')
        classes = [cls.partition(':')[0] for cls in class_base]
        sub_classes = [cls for cls in class_base if cls.split(":")[1]]
        as_classes = elems.pop(0).split(',')

        bgc_classes = [classes, sub_classes, as_classes]        
        chem_classes = [chem_cls.split('; ') for chem_cls in elems[2:]]
        classes_dict[chem_id] = [bgc_classes, chem_classes]

# creating legend from the header
s_h = header.strip().split('\t')
legend_bgc = ['mibig_classes']+s_h[1:3]
legend_chem = s_h[5:]

print(legend_bgc, legend_chem)
print(classes_dict['BGC0000001_abyssomicin C'])

['mibig_classes', 'class:subclass', 'as_classes'] ['cf_kingdom', 'cf_superclass', 'cf_class', 'cf_subclass', 'cf_direct_parent', 'npc_class', 'npc_superclass', 'npc_pathway', 'npc_isglycoside']
[[['Polyketide'], ['Polyketide:Other'], ['T1PKS']], [['Organic compounds'], ['Organoheterocyclic compounds'], ['Oxanes'], [''], ['Oxanes'], ['Spirotetronate macrolides'], ['Macrolides'], ['Polyketides'], ['0']]]


In [9]:
from collections import defaultdict
def rec_dd():
    """Initialises a recurring defaultdict"""
    return defaultdict(rec_dd)

result = rec_dd()
# loop through each mibig compound
for mibig_chem_id, (bgc_classes, chem_classes) in classes_dict.items():
# get all combinations of classes for this compound
    for i, bgc_cat in enumerate(legend_bgc):
        init_bgc_class = bgc_classes[i]
        if not init_bgc_class or init_bgc_class == ['']:
            continue

        bgc_class = init_bgc_class[:]  # if no exceptions, just assign classes

        # do some cleanup for mibig classes
        if bgc_cat == "mibig_classes":
            # group pks-nrp hybrids for MIBiG classes
            hyb_count = len([1 for init_bgc_c in init_bgc_class \
                             if any([test in init_bgc_c.lower() for test in ['nrp', 'pks', 'polyketide']])])
            if hyb_count >= 2:
                # if hybrid, reconstruct the bgc_class
                bgc_class = []
                bgc_class.append("PKS-NRP_Hybrids")
                # append other classes if there are more
                for init_bgc_c in init_bgc_class:
                    if not any([test in init_bgc_c.lower() for test in ['nrp', 'pks', 'polyketide']]):
                        bgc_class.append(init_bgc_c)

            # replace Alkaloid with Other in bgc_class
            bgc_class = ["Other" if bgc_c == "Alkaloid" else bgc_c for bgc_c in bgc_class]

        for j, chem_cat in enumerate(legend_chem):
            chem_class = chem_classes[j]
            if not chem_class or chem_class == ['']:
                continue

            for bgc_c in bgc_class:
                for chem_c in chem_class:
                    try:
                        result[bgc_cat][chem_cat][bgc_c][chem_c] += 1
                    except TypeError:
                        result[bgc_cat][chem_cat][bgc_c][chem_c] = 1

## Display the class matching tables

In [13]:
for name_from, values in result.items():
    for name_to, df_dict in values.items():
        print(f"\n{name_from} -> {name_to}")
        df_count = pd.DataFrame.from_dict(df_dict, dtype=int).fillna(0)
        df = df_count/df_count.sum(axis=0)
        display(df.style.highlight_max(color = 'lightgreen', axis = 0))


mibig_classes -> cf_kingdom



mibig_classes -> cf_superclass



mibig_classes -> cf_class



mibig_classes -> cf_direct_parent



mibig_classes -> npc_class


...


as_classes -> npc_class



as_classes -> npc_superclass



as_classes -> npc_pathway



as_classes -> npc_isglycoside



as_classes -> cf_subclass
